In [28]:
# install biopython on Jupyter server.
import sys
import time
!python -m pip install biopython
from Bio import Entrez
import xml.etree.ElementTree as ET
from urllib.error import HTTPError

Entrez.email = "lszeliga@ethz.ch" # provide your user email 
# RECOMMENDED: apply for API key from NCBI (https://ncbiinsights.ncbi.nlm.nih.gov/2017/11/02/new-api-keys-for-the-e-utilities/). 
# 10 queries per second with a valid API key, otherwise 3 queries per seconds are allowed for 'None'
Entrez.api_key = None

In [29]:
# Get one dbSNP entry and print the XML
# from this then we can design a filter that only leaves the T>C substitutions and removed the entries with C>T

mutation_id = 2154580601
eShandle = Entrez.efetch(db="snp",
                         id=mutation_id,
                         format="xml"
                        )
print(eShandle)
# Read the response content
eSresult = eShandle.read()

# Close the handle
eShandle.close()
print(eSresult)

b'<?xml version="1.0" ?>\n<ExchangeSet xmlns:xsi="https://www.w3.org/2001/XMLSchema-instance" xmlns="https://www.ncbi.nlm.nih.gov/SNP/docsum" xsi:schemaLocation="https://www.ncbi.nlm.nih.gov/SNP/docsum ftp://ftp.ncbi.nlm.nih.gov/snp/specs/docsum_eutils.xsd" ><DocumentSummary uid="2154580601"><SNP_ID>2154580601</SNP_ID><ALLELE_ORIGIN/><GLOBAL_MAFS/><GLOBAL_POPULATION/><GLOBAL_SAMPLESIZE>0</GLOBAL_SAMPLESIZE><SUSPECTED/><CLINICAL_SIGNIFICANCE>pathogenic</CLINICAL_SIGNIFICANCE><GENES><GENE_E><NAME>PCDHGC3</NAME><GENE_ID>5098</GENE_ID></GENE_E><GENE_E><NAME>PCDHGB4</NAME><GENE_ID>8641</GENE_ID></GENE_E><GENE_E><NAME>PCDHGA8</NAME><GENE_ID>9708</GENE_ID></GENE_E><GENE_E><NAME>PCDHGA12</NAME><GENE_ID>26025</GENE_ID></GENE_E><GENE_E><NAME>PCDHGC4</NAME><GENE_ID>56098</GENE_ID></GENE_E><GENE_E><NAME>PCDHGB7</NAME><GENE_ID>56099</GENE_ID></GENE_E><GENE_E><NAME>PCDHGB6</NAME><GENE_ID>56100</GENE_ID></GENE_E><GENE_E><NAME>PCDHGB5</NAME><GENE_ID>56101</GENE_ID></GENE_E><GENE_E><NAME>PCDHGB3</NAME>

In [30]:
## Make the XML easier to read
from xml.dom.minidom import parseString

# Parse the XML data
dom = parseString(eSresult)
# Pretty-print the XML
pretty_xml_as_string = dom.toprettyxml()
# Print the human-readable XML
print(pretty_xml_as_string)

<?xml version="1.0" ?>
<ExchangeSet xmlns:xsi="https://www.w3.org/2001/XMLSchema-instance" xmlns="https://www.ncbi.nlm.nih.gov/SNP/docsum" xsi:schemaLocation="https://www.ncbi.nlm.nih.gov/SNP/docsum ftp://ftp.ncbi.nlm.nih.gov/snp/specs/docsum_eutils.xsd">
	<DocumentSummary uid="2154580601">
		<SNP_ID>2154580601</SNP_ID>
		<ALLELE_ORIGIN/>
		<GLOBAL_MAFS/>
		<GLOBAL_POPULATION/>
		<GLOBAL_SAMPLESIZE>0</GLOBAL_SAMPLESIZE>
		<SUSPECTED/>
		<CLINICAL_SIGNIFICANCE>pathogenic</CLINICAL_SIGNIFICANCE>
		<GENES>
			<GENE_E>
				<NAME>PCDHGC3</NAME>
				<GENE_ID>5098</GENE_ID>
			</GENE_E>
			<GENE_E>
				<NAME>PCDHGB4</NAME>
				<GENE_ID>8641</GENE_ID>
			</GENE_E>
			<GENE_E>
				<NAME>PCDHGA8</NAME>
				<GENE_ID>9708</GENE_ID>
			</GENE_E>
			<GENE_E>
				<NAME>PCDHGA12</NAME>
				<GENE_ID>26025</GENE_ID>
			</GENE_E>
			<GENE_E>
				<NAME>PCDHGC4</NAME>
				<GENE_ID>56098</GENE_ID>
			</GENE_E>
			<GENE_E>
				<NAME>PCDHGB7</NAME>
				<GENE_ID>56099</GENE_ID>
			</GENE_E>
			<GENE_E>
				<NA

Obtain reference and variant nucleotide

In [31]:
# # Parse XML

# Decode the byte string to a regular string
eSresult_str = eSresult.decode('utf-8')
# Parse the XML string
root = ET.fromstring(eSresult_str)
# Define the namespace
ns = {'ns': 'https://www.ncbi.nlm.nih.gov/SNP/docsum'}

# Extract entries
for docsum in root.findall('ns:DocumentSummary', ns):
    snp_id = docsum.find('ns:SNP_ID', ns).text
    clinical_significance = docsum.find('ns:CLINICAL_SIGNIFICANCE', ns).text
    acc = docsum.find('ns:ACC', ns).text
    chrpos = docsum.find('ns:CHRPOS', ns).text
    spdi = docsum.find('ns:SPDI', ns).text
    genes = [gene.find('ns:NAME', ns).text for gene in docsum.findall('ns:GENES/ns:GENE_E', ns)]
    
    print(f"SNP ID: {snp_id}")
    print(f"Clinical Significance: {clinical_significance}")
    print(f"Accession: {acc}")
    print(f"Chromosome Position: {chrpos}")
    print(f"SPDI: {spdi}")
    print(f"Genes: {', '.join(genes)}")
    print()

SNP ID: 2154580601
Clinical Significance: pathogenic
Accession: NC_000005.10
Chromosome Position: 5:141486416
SPDI: NC_000005.10:141486415:C:T
Genes: PCDHGC3, PCDHGB4, PCDHGA8, PCDHGA12, PCDHGC4, PCDHGB7, PCDHGB6, PCDHGB5, PCDHGB3, PCDHGB2, PCDHGB1, PCDHGA11, PCDHGA10, PCDHGA9, PCDHGA7, PCDHGA6, PCDHGA5, PCDHGA4, PCDHGA3, PCDHGA2, PCDHGA1



In [32]:
## Extract last character from spdi
variant_from_spdi = spdi.strip()[-1]
print(variant_from_spdi)

T


Obtain preceeding nucleotide

In [33]:
flank_length = 1
#<CHRPOS>5:141486416</CHRPOS>
chr, pos = chrpos.split(":")
pos = int(pos)
flank_start = pos - flank_length
flank_end = pos + flank_length

lft = Entrez.efetch(db="nuccore", id=acc, rettype="fasta", 
                    seq_start=flank_start, seq_stop=pos-1).read()

In [34]:
## Extract the last character from lft flank
print(lft)
preceeding_nucleotide = lft.strip()[-1]
print(preceeding_nucleotide)

>NC_000005.10:141486415-141486415 Homo sapiens chromosome 5, GRCh38.p14 Primary Assembly
T


T


Get all SNPs that meet the criteria "Y AND pathogenic"

In [72]:
# dbSNP supported query terms (https://www.ncbi.nlm.nih.gov/snp/docs/entrez_help/) can be build and test online using web query builder (https://www.ncbi.nlm.nih.gov/snp/advanced) 
# esearch handle
eShandle = Entrez.esearch(db="snp",  # search dbSNP
                          #complex query for missense and pathogenic variants in LPL gene with global MAF betweeen 0 and 0.01.
                          term='Y[Allele] AND pathogenic[Clinical_Significance]', 
                          usehistory="y", #cache result on server for download in batches
                          retmax=20000 # return 20 RSID max
                         )
# get esearch result
eSresult = Entrez.read(eShandle)

In [73]:
# review results 
for k in eSresult:
    print (k, ":", eSresult[k])
    
#Output: Web environment (&WebEnv) and query key (&query_key) parameters specifying the location on the Entrez history server of the list of UIDs matching the Entrez query
#https://www.ncbi.nlm.nih.gov/books/NBK25500/#chapter1.Storing_Search_Results

Count : 14139
RetMax : 14139
RetStart : 0
QueryKey : 1
WebEnv : MCID_674632283768d2d1410b0498
IdList : ['2154580601', '2154533497', '2154257791', '2154190685', '2154178615', '2154175371', '2154157186', '2154147664', '2154135091', '2154133792', '2154115529', '2154072180', '2154035107', '2154018964', '2153999602', '2153960793', '2153960638', '2153953739', '2153939368', '2153935815', '2153931339', '2153924098', '2153923212', '2153916273', '2153828826', '2153806528', '2153715439', '2153711477', '2153668310', '2153657682', '2153536214', '2153440081', '2153355314', '2153228535', '2153029597', '2153028697', '2153023287', '2153022958', '2153022415', '2153015621', '2152967730', '2152956531', '2152917896', '2152915773', '2152894046', '2152811539', '2152792645', '2152791033', '2152730317', '2152721133', '2152674810', '2152514807', '2152351208', '2152335941', '2152333224', '2152325575', '2152285036', '2152178267', '2152166979', '2152160733', '2152149706', '2152067996', '2152061062', '2152011135', 

In [74]:
variant_ids = eSresult["IdList"]

In [75]:
# get the WebEnv session cookie, and the QueryKey:
webenv = eSresult["WebEnv"]
query_key = eSresult["QueryKey"]
total_count = int(eSresult["Count"])
query_key = eSresult["QueryKey"]
retmax = 40 # return 2 rs per batch example

In [81]:
# list holding all database hits
y_and_pathogenic_unparsed_xml = []

In [86]:
# sample codes adopted with modifications from http://biopython.org/DIST/docs/tutorial/Tutorial.html#htoc139.
fetch_count = 0
for start in range(13160, total_count, retmax):
    end = min(total_count, start+retmax)
    print("Going to download record %i to %i" % (start+1, end))
    variant_id_selection = variant_ids[start:end]
    print(variant_id_selection)
    attempt = 0
    #fetch_count += 1
    while (attempt < 3):
        attempt += 1
        try:
            fetch_handle = Entrez.efetch(db="snp",
                                         id=variant_id_selection,
                                         format="xml"
                                        )
        except HTTPError as err:
            if 500 <= err.code <= 599:
                print("Received error from server %s" % err)
                print("Attempt %i of 3" % attempt)
                time.sleep(15)
            else:
                raise
    if (fetch_handle):
        #print(fetch_handle)            
        data = fetch_handle.read()
        print(data)
        y_and_pathogenic_unparsed_xml.append(data)
        fetch_handle.close()



Going to download record 13161 to 13200
['104893688', '104893678', '104893677', '104893666', '104893659', '104893657', '104893630', '104893627', '104893621', '104893620', '104893613', '104893612', '104886488', '104886306', '104886286', '104886213', '104886094', '80359850', '80359849', '80359841', '80359820', '80359815', '80359814', '80359234', '80358999', '80358851', '80358831', '80358763', '80358374', '80358370', '80358367', '80358308', '80358305', '80358293', '80358289', '80358278', '80358261', '80358258', '80358252', '80358250']
b'<?xml version="1.0" ?>\n<ExchangeSet xmlns:xsi="https://www.w3.org/2001/XMLSchema-instance" xmlns="https://www.ncbi.nlm.nih.gov/SNP/docsum" xsi:schemaLocation="https://www.ncbi.nlm.nih.gov/SNP/docsum ftp://ftp.ncbi.nlm.nih.gov/snp/specs/docsum_eutils.xsd" ><DocumentSummary uid="104893688"><SNP_ID>104893688</SNP_ID><ALLELE_ORIGIN/><GLOBAL_MAFS><MAF><STUDY>1000Genomes</STUDY><FREQ>T=0.000312/2</FREQ></MAF><MAF><STUDY>ExAC</STUDY><FREQ>T=0.000052/6</FREQ></MA

In [87]:
print(len(y_and_pathogenic_unparsed_xml))
# print(y_and_pathogenic_unparsed_xml)

354


In [88]:
y_and_pathogenic_list = []

In [89]:
## Parse each entry in the list and make a list with total_count entries
# # Parse XML

for i in range(len(y_and_pathogenic_unparsed_xml)):
    # Decode the byte string to a regular string
    eSresult_str = y_and_pathogenic_unparsed_xml[i].decode('utf-8')
    # Parse the XML string
    root = ET.fromstring(eSresult_str)
    # Define the namespace
    ns = {'ns': 'https://www.ncbi.nlm.nih.gov/SNP/docsum'}

    # Extract entries
    for docsum in root.findall('ns:DocumentSummary', ns):
        # add the entries into a list -> more like a database now but whatever
        snp_id = docsum.find('ns:SNP_ID', ns).text
        clinical_significance = docsum.find('ns:CLINICAL_SIGNIFICANCE', ns).text
        acc = docsum.find('ns:ACC', ns).text
        chrpos = docsum.find('ns:CHRPOS', ns).text
        spdi = docsum.find('ns:SPDI', ns).text
        genes = [gene.find('ns:NAME', ns).text for gene in docsum.findall('ns:GENES/ns:GENE_E', ns)]

        data = [snp_id, clinical_significance, acc, chrpos, spdi, genes]
        y_and_pathogenic_list.append(data)
        
        print(f"SNP ID: {snp_id}")
        print(f"Clinical Significance: {clinical_significance}")
        print(f"Accession: {acc}")
        print(f"Chromosome Position: {chrpos}")
        print(f"SPDI: {spdi}")
        print(f"Genes: {', '.join(genes)}")
        print()

SNP ID: 2154580601
Clinical Significance: pathogenic
Accession: NC_000005.10
Chromosome Position: 5:141486416
SPDI: NC_000005.10:141486415:C:T
Genes: PCDHGC3, PCDHGB4, PCDHGA8, PCDHGA12, PCDHGC4, PCDHGB7, PCDHGB6, PCDHGB5, PCDHGB3, PCDHGB2, PCDHGB1, PCDHGA11, PCDHGA10, PCDHGA9, PCDHGA7, PCDHGA6, PCDHGA5, PCDHGA4, PCDHGA3, PCDHGA2, PCDHGA1

SNP ID: 2154533497
Clinical Significance: pathogenic
Accession: NC_000001.11
Chromosome Position: 1:20633798
SPDI: NC_000001.11:20633797:C:T
Genes: PINK1, MIR6084

SNP ID: 2154257791
Clinical Significance: pathogenic
Accession: NC_000002.12
Chromosome Position: 2:229789610
SPDI: NC_000002.12:229789609:C:T
Genes: TRIP12

SNP ID: 2154190685
Clinical Significance: pathogenic
Accession: NC_000002.12
Chromosome Position: 2:151671182
SPDI: NC_000002.12:151671181:C:T
Genes: NEB

SNP ID: 2154178615
Clinical Significance: pathogenic
Accession: NC_000002.12
Chromosome Position: 2:178582939
SPDI: NC_000002.12:178582938:C:T
Genes: TTN, TTN-AS1

SNP ID: 215417537

In [90]:
print(len(y_and_pathogenic_list))

14139


Filter now for those SNPs that have T>C and preceeding T

In [94]:
y_and_pathogenic_and_T_to_C_and_preceeding_T = []

In [95]:
flank_length = 1

for i, entry in enumerate(y_and_pathogenic_list):
    snp_id, clinical_significance, acc, chrpos, spdi, genes = entry
    
    ## first reduce the database queries for flanks by filtering for T>C
    
    # Extract the ref:var string from spdi
    variant_from_spdi = spdi.strip()[-3:]
    # if matched with a "T:C", the preceeding nucleotide is looked up
    if variant_from_spdi == "T:C":
        ## lookup the preceeding nucleotide
                
        chr, pos = chrpos.split(":")
        pos = int(pos)
        flank_start = pos - flank_length
        flank_end = pos + flank_length
        
        lft = Entrez.efetch(db="nuccore", id=acc, rettype="fasta", 
                            seq_start=flank_start, seq_stop=pos-1).read()
        preceeding_nucleotide = lft.strip()[-1]
        
        # if matched with a T, the entry is appended to the new database
        if preceeding_nucleotide == 'T':
            print("Iteration", i, "SNP ID:", snp_id)
            y_and_pathogenic_and_T_to_C_and_preceeding_T.append(entry)

Iteration 42 SNP ID: 2152917896
Iteration 98 SNP ID: 2151663957
Iteration 194 SNP ID: 2149388042
Iteration 237 SNP ID: 2148759388
Iteration 238 SNP ID: 2148753700
Iteration 294 SNP ID: 2148352869
Iteration 339 SNP ID: 2147911550
Iteration 354 SNP ID: 2147812145
Iteration 355 SNP ID: 2147808505
Iteration 384 SNP ID: 2147540751
Iteration 386 SNP ID: 2147519384
Iteration 406 SNP ID: 2147404569
Iteration 426 SNP ID: 2147245558
Iteration 443 SNP ID: 2147156094
Iteration 608 SNP ID: 2144739370
Iteration 661 SNP ID: 2143626487
Iteration 764 SNP ID: 2140958637
Iteration 996 SNP ID: 2135404867
Iteration 1075 SNP ID: 2133777379
Iteration 1151 SNP ID: 2131863747
Iteration 1192 SNP ID: 2131001171
Iteration 1212 SNP ID: 2129831435
Iteration 1239 SNP ID: 2129311722
Iteration 1369 SNP ID: 2124131338
Iteration 1438 SNP ID: 2117166533
Iteration 1680 SNP ID: 2104026165
Iteration 1755 SNP ID: 2101106686
Iteration 1837 SNP ID: 2089495673
Iteration 1843 SNP ID: 2087135251
Iteration 1961 SNP ID: 2067192032


In [96]:
print(len(y_and_pathogenic_and_T_to_C_and_preceeding_T))

for entry in y_and_pathogenic_and_T_to_C_and_preceeding_T:
    print(entry)
    print()

396
['2152917896', 'pathogenic', 'NC_000002.12', '2:239144708', 'NC_000002.12:239144707:T:C', ['HDAC4']]

['2151663957', 'pathogenic', 'NC_000017.11', '17:2670188', 'NC_000017.11:2670187:T:C', ['PAFAH1B1']]

['2149388042', 'pathogenic', 'NC_000001.11', '1:237793882', 'NC_000001.11:237793881:T:C', ['RYR2']]

['2148759388', 'pathogenic', 'NC_000002.12', '2:32143349', 'NC_000002.12:32143348:T:C', ['SPAST']]

['2148753700', 'pathogenic', 'NC_000002.12', '2:32136623', 'NC_000002.12:32136622:T:C', ['SPAST']]

['2148352869', 'pathogenic', 'NC_000023.11', 'X:139530743', 'NC_000023.11:139530742:T:C', ['F9']]

['2147911550', 'pathogenic,uncertain-significance', 'NC_000001.11', '1:241498239', 'NC_000001.11:241498238:T:C', ['FH']]

['2147812145', 'pathogenic', 'NC_000001.11', '1:243637634', 'NC_000001.11:243637633:T:C', ['AKT3']]

['2147808505', 'pathogenic', 'NC_000023.11', 'X:71130102', 'NC_000023.11:71130101:T:C', ['MED12']]

['2147540751', 'pathogenic', 'NC_000023.11', 'X:100407852', 'NC_00002

In [97]:
# print a nice list of links that make looking up the SNPs convenient

for entry in y_and_pathogenic_and_T_to_C_and_preceeding_T:
    print(f"https://www.ncbi.nlm.nih.gov/snp/rs{entry[0]}")

https://www.ncbi.nlm.nih.gov/snp/rs2152917896
https://www.ncbi.nlm.nih.gov/snp/rs2151663957
https://www.ncbi.nlm.nih.gov/snp/rs2149388042
https://www.ncbi.nlm.nih.gov/snp/rs2148759388
https://www.ncbi.nlm.nih.gov/snp/rs2148753700
https://www.ncbi.nlm.nih.gov/snp/rs2148352869
https://www.ncbi.nlm.nih.gov/snp/rs2147911550
https://www.ncbi.nlm.nih.gov/snp/rs2147812145
https://www.ncbi.nlm.nih.gov/snp/rs2147808505
https://www.ncbi.nlm.nih.gov/snp/rs2147540751
https://www.ncbi.nlm.nih.gov/snp/rs2147519384
https://www.ncbi.nlm.nih.gov/snp/rs2147404569
https://www.ncbi.nlm.nih.gov/snp/rs2147245558
https://www.ncbi.nlm.nih.gov/snp/rs2147156094
https://www.ncbi.nlm.nih.gov/snp/rs2144739370
https://www.ncbi.nlm.nih.gov/snp/rs2143626487
https://www.ncbi.nlm.nih.gov/snp/rs2140958637
https://www.ncbi.nlm.nih.gov/snp/rs2135404867
https://www.ncbi.nlm.nih.gov/snp/rs2133777379
https://www.ncbi.nlm.nih.gov/snp/rs2131863747
https://www.ncbi.nlm.nih.gov/snp/rs2131001171
https://www.ncbi.nlm.nih.gov/snp/r